In [2]:
import os
import pandas as pd
from openai import OpenAI
from dotenv import load_dotenv

load_dotenv()

client = OpenAI(
    api_key=os.getenv('OPENAI_API_KEY')
)

df=pd.read_pickle('cleaned_quests_with_glossary.pkl')
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 15608 entries, 0 to 15721
Data columns (total 14 columns):
 #   Column          Non-Null Count  Dtype 
---  ------          --------------  ----- 
 0   id              15608 non-null  int64 
 1   expansion       15608 non-null  object
 2   title_en        15608 non-null  object
 3   objective_en    14205 non-null  object
 4   description_en  14212 non-null  object
 5   progress_en     9727 non-null   object
 6   completion_en   15079 non-null  object
 7   title_uk        6280 non-null   object
 8   objective_uk    5414 non-null   object
 9   description_uk  5412 non-null   object
 10  progress_uk     4631 non-null   object
 11  completion_uk   6161 non-null   object
 12  cat             15608 non-null  object
 13  glossary        15608 non-null  object
dtypes: int64(1), object(13)
memory usage: 1.8+ MB


In [3]:
def generate_request_json(row):
    return {
        "original": {
            "quest": {
                "title": row["title_en"],
                "objective": row["objective_en"],
                "description": row["description_en"],
                "progress": row["progress_en"],
                "completion": row["completion_en"]
            }
        },
        "glossary": {
            "glossary": row["glossary"]
        }
    }

def generate_response_json(row):
    return {
        "translation": {
            "quest": {
                "title": row["title_uk"],
                "objective": row["objective_uk"],
                "description": row["description_uk"],
                "progress": row["progress_uk"],
                "completion": row["completion_uk"]
            }
        }
    }


In [4]:
TRANSLATION_SYSTEM_PROMPT = """You are a professional translator specializing in MMORPG game localization, responsible for translating World of Warcraft content from English to Ukrainian. 
You will receive a JSON file containing an "original" section with the object to translate. 
Your task is to respond with a JSON containing single section, "translation", that replicates the structure of the "original" section, replacing source text with translated values while maintaining all keys.
Use your knowledge of the Warcraft universe to ensure accuracy and immersion.

### **Guidelines**:

1. **Preserve Structure**:
   - The output JSON must retain the exact structure of the "original" section.
   - Ensure all keys remain the same while replacing values with their Ukrainian translations.

2. **Maintain Placeholders**:
   - Always replace name/race/class placeholders in the original text with curly-bracedanslated placeholders with shortened Ukrainian grammatical case after a semicolon. For `<name>`, `<race>`, `<class>` use `{ім'я:н}`, `{раса:д}`, `{клас:к}` with correct grammatical case afet semicolon.

3. **Adapt for Gender**:
   - Translate text to be suitable for both genders. For placeholders with gender-specific variations (e.g., `<his/her>`, `<priest/priestess>`) and translated words that have different gender forms use the format `{стать:male:female}` (e.g., `{стать:його:її}`, `{стать:жрець:жриця}`).
   - Gender placeholders should contain full words, so don't break words with placeholder: for example, instead of кмітлив{стать:ий:а} use {стать:кмітливий:кмітлива}
   - Gender placeholders can contain more that one word. If there's several consequent gender-specific placeholders or they are divided with small word - put tham in single placeholder. Fo example: instead of "дуже {стать:достойний:достойна} та {стать:спроможний:спроможна}" use "дуже {стать:достойний та спроможний:достойна та спроможна}"

4. **Formal and Informal Tone**:
   - **Quest `objective` field**: Translate using a formal tone, where "you" becomes "ви" and "your" becomes "ваш".
   - **Quest `description`, `progress`, and `completion` fields**: By default, translate these fields using an informal tone, where "you" becomes "ти" and "your" becomes "твій.". If text describes environment/interaction or NPC speaks to player politely using "sir", "lady" etc - use formal tone.

5. **Preserve Descriptive Formatting**:
   - Retain all text enclosed in angle brackets (`<>`) that describes the environment, character reactions, or similar narrative elements. Translate the content within the brackets but preserve their formatting.

6. **Maintain Lore and Style**:
   - Ensure the translation captures the epic, immersive tone of World of Warcraft.
   - Use established Warcraft terminology and lore-consistent language in Ukrainian.

7. **Glossaries and terminology**:
   - Always strictly refer to the translation glossary. Always use terms' translations from glossary, even if other more commonly used or recognized translations are available.
   - Use consistent terminology throughout all translations. Adhere strictly to any provided glossaries, ensuring uniformity in translating terms such as character names, locations, and game-specific items.

8. **Readability**:
   - Ensure translations are natural, engaging, and free from awkward phrasing.
   - Text should feel native and immersive for Ukrainian-speaking players.

---

### **Input Example**:

```json
{
  "original": {
    "quest": {
      "title": "Get rid of these boars",
      "objective": "Kill 12 boars and return to John at Scarlet Monastery in Silverpine Forest.",
      "description": "Reports have come in that wild boars trample our crops. We thought that other adventurer had dealt with this, <class>!\n\nI suggest that you to teach them a lesson as proof of your devotion.",
      "progress": "Have you clear our fields of wild boars?",
      "completion": "<John nods to you.>\n\nWe are pleased that you have prooved your devition, <name>. Surely now that you have made our point clear multiple times, their senseless attacks upon our crops will cease?"
    }
  }
}
```

---

### **Output Example**:

```json
{
  "translation": {
    "quest": {
      "title": "Позбудься цих вепрів",
      "objective": "Вбийте 12 вепрів і поверніться до Джона в Багряний Монастир, що в Срібнохвойному пралісі.",
      "description": "Надходять повідомлення про диких вепрів, що топчуть наші посіви. Ми думали, що інші шукачі пригод вже розібралися з цим, {клас:к}!\n\nРаджу тобі провчити їх як доказ твоєї відданості.",
      "progress": "Ти вже {стать:очистив:очистила} наші поля від диких вепрів?",
      "completion": "<Джон киває вам.>\n\nМи задоволені, що ти {стать:довів:довела} свою відданість, {ім'я:к}. Тепер, коли ми вже неодноразово довели свою точку зору, може їхні безглузді напади на наші посіви припиняться?"
    }
  }
}
```

---
"""

In [6]:
filtered_quests = df[df['description_uk'].str.contains(r'\:р}', na=False)]
filtered_quests.head()

id expansion             title_en  \
314    334   classic  Package for Thurman   
812    861   classic     The Hunter's Way   
1298  1498   classic      Path of Defense   
1315  1516   classic        Call of Earth   
1372  1679   classic      Muren Stormpike   

                                           objective_en  \
314   Go to the Larson Clothiers in the Stormwind Ma...   
812   Bring 4 Flatland Prowler Claws to Melor Stoneh...   
1298  Bring 5 Singed Scales to Uzzek at Far Watch Po...   
1315  Bring 2 Felstalker Hooves to Canaga Earthcalle...   
1372                        Speak with Muren Stormpike.   

                                         description_en  \
314   My son Thurman is an apprentice at the Larson ...   
812   You are eager to explore, I can tell. I too ha...   
1298  As a warrior, one of our most crucial tasks is...   
1315  The time is now, young <class>. You've grown s...   
1372  Hello, warrior! You show a lot of promise, but...   

                                            progress_en  \
314                        Are you here to buy clothes?   
812   Greetings. There is an air about you that tell...   
1298  Do you have the scales, <name>? Unless you can...   
1315  Patience is earth's greatest virtue. The earth...   
1372                                               None   

                                          completion_en             title_uk  \
314   Oh, blast! I thought forgetting my kit would f...  Пакунок для Турмана   
812   Skorn Whitecloud is a wise <race>. He has hunt...        Шлях мисливця   
1298  Ah. I see you have defeated the thunder lizard...    Мистецтво захисту   
1315  Excellent. Your success shows that you are pre...         Поклик землі   
1372  Ah, <name>. I heard the warriors of Dun Morogh...      Мурен Бурешпиль   

                                           objective_uk  \
314   Відправляйтесь в "сукна Ларсона", що у квартал...   
812   Принесіть 4 пазури рівнинного скрадача Мелоров...   
1298  Принесіть 5 припалених лусок Узеку на Далекост...   
1315  Принесіть 2 копита скверноловів Каназі Землезо...   
1372                   Поговоріть з Муреном Бурешпилем.   

                                         description_uk  \
314   Мій син Турман — учень в "сукнах Ларсона", що ...   
812   А ти {стать:охочий:охоча} до мандрівок, я можу...   
1298  Одна з твоїх найважливіших задач, як {клас:р}....   
1315  Час прийшов, {стать:юний:юна} {клас:к}. Твої с...   
1372  Вітаю, {клас:к}! Ти непогано себе {стать:прояв...   

                                            progress_uk  \
314                         Вітаю! Бажаєте щось купити?   
812   Вітаю. Твоя присутність багато про що говорить...   
1298  {стать:Приніс:Принесла} луску, {ім'я:к}? Якщо ...   
1315  Терпіння — найбільша чеснота землі. Земля є св...   
1372                                               None   

                                          completion_uk  \
314   Ой, ле! Я думав, що, забувши інструменти, я зм...   
812   Скорн Біла Хмара - мудрий таурен. Він полював ...   
1298  А-а-а, бачу, ти {стать:поборов:поборола} громо...   
1315  Чудово. Твій успіх доводить, що ти {стать:гото...   
1372  А, {ім'я}. Чув я щось про тебе від воїнів Дун-...   

                                  cat  \
314   Eastern Kingdoms/Stormwind City   
812                  Kalimdor/Mulgore   
1298                  Classes/Warrior   
1315                   Classes/Shaman   
1372                  Classes/Warrior   

                                               glossary  
314   [{'en': 'Stormwind', 'uk': 'Штормовій'}, {'en'...  
812   [{'en': 'Mulgore', 'uk': 'Мулґор'}, {'en': 'Th...  
1298  [{'en': 'The Horde', 'uk': 'Орда'}, {'en': 'Ba...  
1315  [{'en': 'Valley of Trials', 'uk': 'долина Випр...  
1372  [{'en': 'Dun Morogh', 'uk': 'Дун-Морог'}, {'en...

In [16]:
quest_row = filtered_quests.iloc[0]
quest_row['glossary']

[{'en': 'Stormwind', 'uk': 'Штормовій'},
 {'en': 'mage', 'uk': 'маг/магиня'},
 {'en': 'apprentice', 'uk': 'учень'},
 {'en': 'Thurman Schneider', 'uk': 'Турман Шнайдер'}]

In [11]:
messages = [{'role': 'system', 'content': TRANSLATION_SYSTEM_PROMPT}, {'role': 'user', 'content': str(generate_request_json(quest_row))}]

response = client.chat.completions.create(
  model="gpt-4o",
  # model="gpt-4o-mini",
  # model="ft:gpt-4o-mini-2024-07-18:personal:classicua-trained-3:AXaw8vp9",
  # model="gpt-3.5-turbo",
  messages=messages,
  response_format={"type":"json_object"},
  temperature=0.5,
  top_p=0.7
)

# print(response.choices[0].message)
import json
json_response = response.choices[0].message.content
json.loads(json_response)['translation']

{'quest': {'title': 'Посилка для Турмана',
  'objective': 'Вирушайте до Кравців Ларсонів у кварталі магів Штормовію та віддайте Турману Шнайдеру його набір для шиття.',
  'description': "Мій син Турман - учень у Кравців Ларсонів, що в кварталі магів. Сьогодні він поспішав і забув свої ножиці та голки. Я знаю, що великий {клас:к} як ти, мабуть, має важливі завдання, але без своїх інструментів Турман не може виконувати свою учнівську роботу!\n\nБудь ласка, {ім'я:н}. Чи можеш ти віднести набір для шиття мого сина йому? Кравці Ларсонів - один з двох магазинів одягу в кварталі магів - це той, що глибше, біля Вежі магів.",
  'progress': 'Ви тут, щоб купити одяг?',
  'completion': 'О, біда! Я думав, що забувши свій набір, звільнюсь від роботи. Тепер, мабуть, доведеться допомагати Ларсонам з їхнім шиттям...\n\nНу, гаразд. Розваги, мабуть, прийдуть пізніше.'}}

In [18]:
translated = df[df['title_uk'].notnull()]
untranslated = df[df['title_uk'].isnull()]
translated.head()

id expansion                   title_en  \
0   2   classic          Sharptalon's Claw   
1   5   classic      Jitters' Growling Gut   
2   6   classic  Bounty on Garrick Padfoot   
3   7   classic        Kobold Camp Cleanup   
4   8   classic             A Rogue's Deal   

                                        objective_en  \
0  Bring Sharptalon's Claw to Senani Thunderheart...   
1                             Speak with Chef Grual.   
2  Kill Garrick Padfoot and bring his head to Dep...   
3  Kill 10 Kobold Vermin, then return to Marshal ...   
4  Deliver the Nondescript Letter to Innkeeper Re...   

                                      description_en  \
0  The mighty hippogryph Sharptalon has been slai...   
1  I've been stuck hiding in this ghost town for ...   
2  Garrick Padfoot - a cutthroat who's plagued ou...   
3  Your first task is one of cleansing, <name>. A...   
4  Hey, mate! Do a favor for a young man who's be...   

                                         progress_en  \
0  Yes, mighty <class>, I sensed your arrival. I ...   
1                                               None   
2  Did you find Garrick's shack? Are we finally f...   
3  How goes the hunting, <name>? Have you found a...   
4  Yes? Yes? What is it?\n\nThe forsaken; they ce...   

                                       completion_en  \
0  Most impressive, <name>... the claw of Sharpta...   
1  You need some Crab Cakes, do you? Well I might...   
2  Hah - you caught him! You've done Elwynn a gre...   
3  Well done, citizen. Those kobolds are thieves ...   
4  Oh? A letter? Wonderful news! I've been waitin...   

                                  title_uk  \
0                      Кіготь Гостропазура   
1            Бурчання Тремтінієвого живота   
2  Винагорода за голову Ґарріка М'якоступа   
3                Зачистка табору кобольдів   
4                        Угода пройдисвіта   

                                        objective_uk  \
0  Принесіть кіготь Гостропазура до Сенані Грозов...   
1                  Поговоріть з шеф-кухарем Ґруалем.   
2  Убийте Ґарріка М'якоступа та принесіть його го...   
3  Убийте 10 кобольдів-шкідників, а потім поверні...   
4  Доставте непідписаний лист корчмарці Рені в Ті...   

                                      description_uk  \
0  Могутнього Гостропазура вбито, а кіготь гіпогр...   
1  Я вже декілька тижнів ховаюсь в цьому містечку...   
2  Ґаррік М'якоступ — головоріз, який мучить наши...   
3  Твоє перше завдання буде пов'язане із зачищенн...   
4  Гей, {стать:приятелю:приятелько}! Зроби-но пос...   

                                         progress_uk  \
0  Так, {стать:могутній:могутня} {клас:к}, я відч...   
1                                               None   
2  Ти {стать:знайшов:знайшла} халупу Ґарріка? Нев...   
3  Як там твоє полювання, {ім'я:к}? Ти {стать:зна...   
4  Так? Так? Що це?\n\nВідречені. У них, безумовн...   

                                       completion_uk  \
0  Я вражена, {ім'я:к}... кіготь Гостропазура — н...   
1  Хочеш крабових пиріжків? Ну, я можу приготуват...   
2  Ха-а — ти {стать:спіймав:спіймала} його! Ти {с...   
3  Молодець, {стать:громадянине:громадянко}. Ці к...   
4  Га? Лист? Гарні новини! Я так чекала на звістк...   

                                cat  \
0                Kalimdor/Ashenvale   
1         Eastern Kingdoms/Duskwood   
2    Eastern Kingdoms/Elwynn Forest   
3    Eastern Kingdoms/Elwynn Forest   
4  Eastern Kingdoms/Tirisfal Glades   

                                            glossary  
0  [{'en': 'Ashenvale', 'uk': 'Ясенеділ'}, {'en':...  
1  [{'en': 'cook', 'uk': 'кухар/кухарка'}, {'en':...  
2  [{'en': 'deputy', 'uk': 'заступник'}, {'en': '...  
3  [{'en': 'kobold', 'uk': 'кобольд'}, {'en': 'St...  
4  [{'en': 'innkeeper', 'uk': 'корчмар/корчмарка'...

In [23]:
def construct_prompt_completion(quest_row):
    messages = [{'role': 'system', 'content': TRANSLATION_SYSTEM_PROMPT}, {'role': 'user', 'content': str(generate_request_json(quest_row))}, {'role': 'assistant', 'content': str(generate_response_json(quest_row))}]
    return {"messages": messages}

jsonl_data = translated.apply(construct_prompt_completion, axis=1).tolist()
jsonl_data

[{'messages': [{'role': 'system',
    'content': 'You are a professional translator specializing in MMORPG game localization, responsible for translating World of Warcraft content from English to Ukrainian. \nYou will receive a JSON file containing an "original" section with the object to translate. \nYour task is to respond with a JSON containing single section, "translation", that replicates the structure of the "original" section, replacing source text with translated values while maintaining all keys.\nUse your knowledge of the Warcraft universe to ensure accuracy and immersion.\n\n### **Guidelines**:\n\n1. **Preserve Structure**:\n   - The output JSON must retain the exact structure of the "original" section.\n   - Ensure all keys remain the same while replacing values with their Ukrainian translations.\n\n2. **Maintain Placeholders**:\n   - Always replace name/race/class placeholders in the original text with curly-bracedanslated placeholders with shortened Ukrainian grammatical 

In [24]:
# %pip install tiktoken
import tiktoken

def num_tokens_from_string(string: str, encoding_name:str="cl100k_base") -> int:
    encoding = tiktoken.get_encoding(encoding_name)
    num_tokens = len(encoding.encode(string))
    return num_tokens

num_tokens_from_string(str(jsonl_data))

14903278

In [29]:
# Meticulously chosen and refined translations with various cases for pre-training:
pre_training_quest_ids = [(22, "classic"), (60, "classic"),(188, "classic"),(230, "classic"),(334, "classic"),(365, "classic"),(575, "classic"),(595, "classic"),(663, "wrath"),(752, "classic"),(753, "classic"),(884, "classic"),(902, "classic"),(1140, "classic"),(1718, "classic"),(2278, "classic"),(2279, "classic"),(2280, "classic"),(2358, "wrath"),(2947, "classic"),(2949, "classic"),(2978, "classic"),(3741, "classic"),(3942, "classic"),(4602, "classic"),(4603, "classic"),(5210, "classic"),(5943, "classic"),(9393, "tbc"),(9402, "tbc"),(9488, "tbc"),(9523, "tbc"),(9558, "tbc"),(9595, "tbc"),(9616, "tbc"),(9646, "tbc"),(9649, "tbc"),(9696, "tbc"),(9797, "tbc"),(10065, "tbc"),(77643, "sod")]
# Some more data for pre-training:
additional_pre_training_quest_ids = [(2, "classic"),(5, "classic"),(6, "classic"),(7, "classic"),(8, "classic"),(9, "classic"),(10, "classic"),(11, "classic"),(12, "classic"),(13, "classic"),(14, "classic"),(15, "classic"),(17, "classic"),(18, "classic"),(19, "classic"),(20, "classic"),(21, "classic"),(23, "classic"),(24, "classic"),(25, "classic"),(26, "classic"),(28, "classic"),(33, "classic"),(34, "classic"),(35, "classic"),(36, "classic"),(37, "classic"),(38, "classic"),(39, "classic"),(40, "classic"),(45, "classic"),(46, "classic"),(47, "classic"),(52, "classic"),(54, "classic"),(55, "classic"),(56, "classic"),(57, "classic"),(58, "classic"),(59, "classic"),(62, "classic"),(64, "classic"),(65, "classic"),(66, "classic"),(67, "classic"),(68, "classic"),(69, "classic"),(70, "classic"),(71, "classic"),(72, "classic"),(74, "classic"),(75, "classic"),(76, "classic"),(85, "classic"),(85, "classic"),(86, "classic"),(87, "classic"),(88, "classic"),(89, "classic")]

filter_df = pd.DataFrame([*pre_training_quest_ids, *additional_pre_training_quest_ids], columns=["id", "expansion"])
pre_training_quests = translated.merge(filter_df, on=["id", "expansion"])

In [27]:
translated_outland = translated[translated['cat'].isin(("Outland/Hellfire Peninsula", "Outland/Zangarmarsh"))]
translated_outland

id expansion                     title_en  \
5297   9340       tbc            The Great Fissure   
5298   9345       tbc          Preparing the Salve   
5299   9349       tbc          Ravager Egg Roundup   
5300   9351       tbc        Voidwalkers Gone Wild   
5302   9354       tbc  Searching for New Materials   
...     ...       ...                          ...   
6714  10937       tbc        Drill the Drillmaster   
7353  13408       tbc      Hellfire Fortifications   
7354  13409       tbc      Hellfire Fortifications   
7355  13410       tbc      Hellfire Fortifications   
7356  13411       tbc      Hellfire Fortifications   

                                           objective_en  \
5297  Ranger Captain Venn'ren at Falcon Watch wants ...   
5298  Gather 12 Hellfire Spineleaf plants for a salv...   
5299  Retrieve 12 Ravager Eggs for Legassi at the Ze...   
5300  Bring 10 Condensed Voidwalker Essences to "Scr...   
5302  Gather 8 Clefthoof Hides and 8 Clefthoof Sinew...   
...                                                 ...   
6714  Force Commander Danath Trollbane has ordered y...   
7353  Capture the Overlook, the Stadium and Broken H...   
7354  Capture the Overlook, the Stadium and Broken H...   
7355  Capture the Overlook, the Stadium and Broken H...   
7356  Capture the Overlook, the Stadium and Broken H...   

                                         description_en  \
5297  We're dangerously close to becoming fenced in ...   
5298  Just as Zeth'Gor came into view, a Legion patr...   
5299  I'm starving!\n\nThere's irony in that, wouldn...   
5300  Even if I can get the zeppelin's frame repaire...   
5302  <The dwarf looks up from his work expectantly....   
...                                                 ...   
6714  I'm receiving reports that the Shattered Hand ...   
7353  The Hellfire Citadel wages constant battles wi...   
7354  The fel orcs of Hellfire Citadel must be scour...   
7355  The Hellfire Citadel wages constant battles wi...   
7356  The fel orcs of Hellfire Citadel must be scour...   

                                            progress_en  \
5297                 You've returned. Is the task done?   
5298                       Have you brought the plants?   
5299  You have those eggs yet?\n\n<Legassi's stomach...   
5300                  Were you able to get the essence?   
5302                                               None   
...                                                 ...   
6714  Is the drillmaster dead? Hmm, maybe my scouts ...   
7353  <name>, return to me when you have aided in th...   
7354  Return to me after you have helped capture eac...   
7355                                               None   
7356  Return to me after you have helped capture eac...   

                                          completion_en  \
5297  Good job, <name>. That should teach the rock f...   
5298  These should do the job. I'm going to prepare ...   
5299  In order to have great cuisine, you need to ha...   
5300  This is perfect! In fact, I think it's going t...   
5302                                               None   
...                                                 ...   
6714  I wasn't going to believe it until I heard it ...   
7353  Well done, <name>. Your actions in the field a...   
7354  Nice work, <name>. I could almost hear the bat...   
7355  Well done, <name>. Your actions in the field a...   
7356  Nice work, <name>. I could almost hear the bat...   

                         title_uk  \
5297               Великий розлом   
5298            Виготовлення мазі   
5299       Збір яєць спустошників   
5300         Здичавілі пустотники   
5302       Пошук нових матеріалів   
...                           ...   
6714   Вбити бойового інструктора   
7353  Укріплення Пекельного Вогню   
7354  Укріплення Пекельного Вогню   
7355  Укріплення Пекельного Вогню   
7356  Укріплення Пекельного Вогню   

                                           objective_uk  \
5297  Капітан слідоп

In [31]:
pretrain_outland = pd.concat([pre_training_quests, translated_outland], ignore_index=True)
pretrain_outland

id expansion                   title_en  \
0        2   classic          Sharptalon's Claw   
1        5   classic      Jitters' Growling Gut   
2        6   classic  Bounty on Garrick Padfoot   
3        7   classic        Kobold Camp Cleanup   
4        8   classic             A Rogue's Deal   
..     ...       ...                        ...   
367  10937       tbc      Drill the Drillmaster   
368  13408       tbc    Hellfire Fortifications   
369  13409       tbc    Hellfire Fortifications   
370  13410       tbc    Hellfire Fortifications   
371  13411       tbc    Hellfire Fortifications   

                                          objective_en  \
0    Bring Sharptalon's Claw to Senani Thunderheart...   
1                               Speak with Chef Grual.   
2    Kill Garrick Padfoot and bring his head to Dep...   
3    Kill 10 Kobold Vermin, then return to Marshal ...   
4    Deliver the Nondescript Letter to Innkeeper Re...   
..                                                 ...   
367  Force Commander Danath Trollbane has ordered y...   
368  Capture the Overlook, the Stadium and Broken H...   
369  Capture the Overlook, the Stadium and Broken H...   
370  Capture the Overlook, the Stadium and Broken H...   
371  Capture the Overlook, the Stadium and Broken H...   

                                        description_en  \
0    The mighty hippogryph Sharptalon has been slai...   
1    I've been stuck hiding in this ghost town for ...   
2    Garrick Padfoot - a cutthroat who's plagued ou...   
3    Your first task is one of cleansing, <name>. A...   
4    Hey, mate! Do a favor for a young man who's be...   
..                                                 ...   
367  I'm receiving reports that the Shattered Hand ...   
368  The Hellfire Citadel wages constant battles wi...   
369  The fel orcs of Hellfire Citadel must be scour...   
370  The Hellfire Citadel wages constant battles wi...   
371  The fel orcs of Hellfire Citadel must be scour...   

                                           progress_en  \
0    Yes, mighty <class>, I sensed your arrival. I ...   
1                                                 None   
2    Did you find Garrick's shack? Are we finally f...   
3    How goes the hunting, <name>? Have you found a...   
4    Yes? Yes? What is it?\n\nThe forsaken; they ce...   
..                                                 ...   
367  Is the drillmaster dead? Hmm, maybe my scouts ...   
368  <name>, return to me when you have aided in th...   
369  Return to me after you have helped capture eac...   
370                                               None   
371  Return to me after you have helped capture eac...   

                                         completion_en  \
0    Most impressive, <name>... the claw of Sharpta...   
1    You need some Crab Cakes, do you? Well I might...   
2    Hah - you caught him! You've done Elwynn a gre...   
3    Well done, citizen. Those kobolds are thieves ...   
4    Oh? A letter? Wonderful news! I've been waitin...   
..                                                 ...   
367  I wasn't going to believe it until I heard it ...   
368  Well done, <name>. Your actions in the field a...   
369  Nice work, <name>. I could almost hear the bat...   
370  Well done, <name>. Your actions in the field a...   
371  Nice work, <name>. I could almost hear the bat...   

                                    title_uk  \
0                        Кіготь Гостропазура   
1              Бурчання Тремтінієвого живота   
2    Винагорода за голову Ґарріка М'якоступа   
3                  Зачистка табору кобольдів   
4                          Угода пройдисвіта   
..                                       ...   
367               Вбити бойового інструктора   
368              Укріплення Пекельного Вогню   
369              Укріплення Пекельного Вогню   
370              Укріплення Пекельного Вогню   
371              Укріплення Пекельного Вогню   

                              

In [34]:
jsonl_data = pretrain_outland.apply(construct_prompt_completion, axis=1).tolist()
num_tokens_from_string(str(jsonl_data))

911133

In [35]:
import json

with open('pre_training_data.jsonl', 'w', encoding='utf-8') as f:
    for entry in jsonl_data[:300]:
        json.dump(entry, f, ensure_ascii=False)
        f.write('\n')

with open('pre_training_validation.jsonl', 'w', encoding='utf-8') as f:
    for entry in jsonl_data[300:]:
        json.dump(entry, f, ensure_ascii=False)
        f.write('\n')

In [36]:
with open('test.json', 'w', encoding='utf-8') as f:
    json.dump(generate_request_json(untranslated.iloc[3]), f, ensure_ascii=False)

# From there we'll use OpenAI dashboard for fine-tuning